In [393]:
import os
import zipfile
import pandas as pd
import numpy as np
import plotly.express as px
import matplotlib.pyplot as plt
from scipy.stats import zscore
from sklearn.preprocessing import OrdinalEncoder
%matplotlib inline

## Download dataset

In [2]:
if not os.listdir('../input'):
    !kaggle competitions download -c cs5228-2022-semester-1-final-project -p ../input
    Dataset = "cs5228-2022-semester-1-final-project"
    with zipfile.ZipFile(f"../input/{Dataset}.zip","r") as z:
        z.extractall("../input")

In [113]:
for dirname, _, filenames in os.walk('../input'):
    for filename in filenames:
        if filename.endswith('csv'):
            print(os.path.join(dirname, filename))

../input\example-submission.csv
../input\test.csv
../input\train.csv
../input\auxiliary-data\sg-commerical-centres.csv
../input\auxiliary-data\sg-mrt-stations.csv
../input\auxiliary-data\sg-primary-schools.csv
../input\auxiliary-data\sg-secondary-schools.csv
../input\auxiliary-data\sg-shopping-malls.csv
../input\auxiliary-data\sg-subzones.csv


### train.csv

In [230]:
train_df = pd.read_csv('../input/train.csv')
train_df.head(2)

listing_id                                              title  \
0      122881          hdb flat for sale in 866 yishun street 81   
1      259374  hdb flat for sale in 506b serangoon north aven...   

                              address         property_name property_type  \
0            sembawang / yishun (d27)  866 yishun street 81   hdb 4 rooms   
1  hougang / punggol / sengkang (d19)  hdb-serangoon estate           hdb   

              tenure  built_year  num_beds  num_baths  size_sqft  ...  \
0                NaN      1988.0       3.0        2.0       1115  ...   
1  99-year leasehold      1992.0       4.0        2.0       1575  ...   

    furnishing available_unit_types total_num_units  \
0  unspecified                  NaN           116.0   
1  unspecified  1, 2, 3, 4, 5, 6 br             NaN   

                                property_details_url       lat         lng  \
0  https://www.99.co/singapore/hdb/866-yishun-str...  1.414399  103.837196   
1  https://www.99.co/singapore/hdb/hdbserangoon-e...  1.372597  103.875625   

   elevation          subzone planning_area     price  
0          0     yishun south        yishun  514500.0  
1          0  serangoon north     serangoon  995400.0  

[2 rows x 21 columns]

In [231]:
print(train_df.shape)
display(train_df.isnull().sum())
display(train_df.describe())

(20254, 21)


listing_id                  0
title                       0
address                     0
property_name               0
property_type               0
tenure                   1723
built_year                922
num_beds                   80
num_baths                 434
size_sqft                   0
floor_level             16746
furnishing                  0
available_unit_types     1441
total_num_units          5652
property_details_url        0
lat                         0
lng                         0
elevation                   0
subzone                   113
planning_area             113
price                       0
dtype: int64

listing_id    built_year      num_beds     num_baths     size_sqft  \
count   20254.000000  19332.000000  20174.000000  19820.000000  2.025400e+04   
mean   550763.206428   2010.833695      3.122931      2.643542  1.854364e+03   
std    258874.420108     15.822803      1.281658      1.473835  1.354343e+04   
min    100043.000000   1963.000000      1.000000      1.000000  0.000000e+00   
25%    326279.000000   2000.000000      2.000000      2.000000  8.070000e+02   
50%    551397.000000   2017.000000      3.000000      2.000000  1.119000e+03   
75%    774044.500000   2023.000000      4.000000      3.000000  1.528000e+03   
max    999944.000000   2028.000000     10.000000     10.000000  1.496000e+06   

       total_num_units           lat           lng  elevation         price  
count     14602.000000  20254.000000  20254.000000    20254.0  2.025400e+04  
mean        376.253938      1.434282    103.855356        0.0  5.228263e+06  
std         346.882474      1.558472      3.593441        0.0  2.779748e+08  
min           4.000000      1.239621    -77.065364        0.0  0.000000e+00  
25%         106.000000      1.307329    103.806576        0.0  8.190000e+05  
50%         296.000000      1.329266    103.841552        0.0  1.680000e+06  
75%         561.000000      1.372461    103.881514        0.0  3.242400e+06  
max        2612.000000     69.486768    121.023232        0.0  3.924243e+10

In [399]:
fig = px.histogram(train_df, x='price')
fig.show()

In [431]:
def remove_price_outlier(df) -> pd.DataFrame:
    df_ = df.copy()
    df_.drop(df_[zscore(df_['price']) > 3].index, inplace=True)
    return df_

In [432]:
train_df_clean = remove_price_outlier(train_df)
fig = px.histogram(train_df_clean, x='price')
fig.show()

### test.csv

In [232]:
test_df = pd.read_csv('../input/test.csv')
test_df.head(1)

listing_id                                title           address  \
0      777912  1 bed condo for sale in the gazania  17 how sun drive   

  property_name property_type    tenure  built_year  num_beds  num_baths  \
0   the gazania         condo  freehold      2022.0       1.0        1.0   

   size_sqft floor_level   furnishing      available_unit_types  \
0        463         NaN  unfurnished  studio, 1, 2, 3, 4, 5 br   

   total_num_units                               property_details_url  \
0            250.0  https://www.99.co/singapore/condos-apartments/...   

        lat        lng  elevation           subzone planning_area  
0  1.344334  103.87869          0  upper paya lebar     serangoon

In [233]:
print(test_df.shape)
display(test_df.isnull().sum())
display(test_df.describe())

(7000, 20)


listing_id                 0
title                      0
address                    2
property_name              0
property_type              0
tenure                   637
built_year               358
num_beds                  35
num_baths                152
size_sqft                  0
floor_level             5844
furnishing                 0
available_unit_types     520
total_num_units         1900
property_details_url       0
lat                        0
lng                        0
elevation                  0
subzone                   33
planning_area             33
dtype: int64

listing_id   built_year     num_beds    num_baths     size_sqft  \
count    7000.000000  6642.000000  6965.000000  6848.000000   7000.000000   
mean   551687.994143  2010.823999     3.089591     2.624854   1709.027000   
std    259038.092508    15.713629     1.276983     1.466597   1860.113894   
min    100108.000000  1963.000000     1.000000     1.000000     68.000000   
25%    327927.000000  2000.000000     2.000000     2.000000    797.000000   
50%    549475.000000  2017.000000     3.000000     2.000000   1119.000000   
75%    775229.000000  2023.000000     4.000000     3.000000   1528.000000   
max    999981.000000  2028.000000    10.000000    10.000000  27500.000000   

       total_num_units          lat          lng  elevation  
count      5100.000000  7000.000000  7000.000000     7000.0  
mean        373.181373     1.416640   103.853102        0.0  
std         333.976046     1.343290     3.408832        0.0  
min           6.000000     1.239621   -77.065364        0.0  
25%         111.000000     1.307189   103.806576        0.0  
50%         298.000000     1.329266   103.842241        0.0  
75%         561.000000     1.370798   103.879948        0.0  
max        2612.000000    69.486768   121.023232        0.0

#### Data fields
* listing_id - unique identifier of the property listing
* title - title of the property listing (e.g., "2 bed condo for sale in 35 gilstead")
* address - address of the property (e.g., "124 punggol walk", "11 sengkang east avenue")
* property_name - name of the property (e.g., "redhill rise", "klimt cairnhill")
* property_type - type of the property (e.g., "condo", "hdb 2 rooms", "landed")
* tenure - tenure of the property (e.g., "freehold", "99-year leasehold")
* built_year - year when the property was was built (e.g., 2014, 2021)
* num_beds - number of bedrooms (e.g., 1, 2, 3)
* num_baths - number of bathrooms (e.g., 1, 2, 3)
* size_sqft - floor area in square feet (e.g., 807, 657, 1628)
* floor_level - information about the floor level of the property (e.g., "high", "low")
* furnishing - information whether the property is furnished (e.g., "fully", "partial")
* available_unit_types - list of all types of units available in the property complex (e.g., "studio, 3, 4, 5 br")
* total_num_units - total number of units in the property complex (e.g., 115, 200)
* property_details_url - URL linking to more information about the property complex
* lat - latitude of property (e.g., 1.328805)
* lng - longitude of property (e.g., 103.74502)
* elevation - elevation of the property in meters (e.g., 10)
* subszone - subzone of block containing the flat in meter (e.g., "blangah rise", "marymount")
* planning_area - planning area of block containing the flat (e.g., "woodlands", "bukit merah")
* price - sales price in SGD

In [433]:
train_df_clean.head(1)

listing_id                                      title  \
0      122881  hdb flat for sale in 866 yishun street 81   

                    address         property_name property_type tenure  \
0  sembawang / yishun (d27)  866 yishun street 81   hdb 4 rooms    NaN   

   built_year  num_beds  num_baths  size_sqft  ...  \
0      1988.0       3.0        2.0       1115  ...   

                                property_details_url       lat         lng  \
0  https://www.99.co/singapore/hdb/866-yishun-str...  1.414399  103.837196   

   elevation       subzone  planning_area     price  title_property_type  \
0          0  yishun south         yishun  514500.0             hdb flat   

  title_n_beds         title_address  
0     hdb flat  866 yishun street 81  

[1 rows x 24 columns]

In [434]:
for col in train_df_clean.columns[1:]:
    """ list all columns' histograms
    """
    print(col)
    # fig = px.histogram(train_df_clean, x=col)
    # fig.show()

title
address
property_name
property_type
tenure
built_year
num_beds
num_baths
size_sqft
floor_level
furnishing
available_unit_types
total_num_units
property_details_url
lat
lng
elevation
subzone
planning_area
price
title_property_type
title_n_beds
title_address


In [435]:
drop_attributes = {'listing_id'}

## auxiliary data

In [436]:
for dirname, _, filenames in os.walk('../input/auxiliary-data/'):
    for filename in filenames:
        if filename.endswith('csv'):
            print(os.path.join(dirname, filename))
            aux_df = pd.read_csv(os.path.join(dirname, filename))
            display(aux_df.head(1))

../input/auxiliary-data/sg-commerical-centres.csv


name type       lat         lng        subzone  \
0  Central Business District   CR  1.286768  103.854529  clifford pier   

   planning_area  
0  downtown core

../input/auxiliary-data/sg-mrt-stations.csv


code line         name  opening_year       lat         lng      subzone  \
0  cc1   cc  dhoby ghaut          2010  1.298912  103.846293  dhoby ghaut   

  planning_area  
0        museum

../input/auxiliary-data/sg-primary-schools.csv


...

name       lat         lng         subzone  \
0  Admiralty Secondary School  1.445912  103.802908  woodlands east   

  planning_area  
0     woodlands

../input/auxiliary-data/sg-shopping-malls.csv


name       lat         lng       subzone planning_area
0  10 AM  1.275568  103.863591  marina south  marina south

../input/auxiliary-data/sg-subzones.csv


name  area_size  population planning_area
0  ang mo kio town centre     0.3169        4810    ang mo kio

## 1. title
* no missing value
* containing following attributes (overlapped with other fields):
    1. property_type
    2. for sale
    3. location
* usage:
    1. not useful for modeling
    2. sanity check for other attributes (address, )
    3. impute for other attributes
        * num_beds: 80 NaN
        * subzone/ planning_area: 113 NaN

In [437]:
def extract_title_info(df) -> pd.DataFrame:
    df_ = df.copy()
    """get property_type form title
    """
    df_['title_property_type'] = df_['title'].str.split(' for').str[0].str.split('bed').str[-1].str.strip()
    """get num bed form title
    """
    df_['title_n_beds'] = df_['title'].str.split(' for').str[0].str.split('bed').str[0].str.strip()
    """ check is all sale
    """
    print(df_['title'].str.split('for ').str[-1].str.split(' ').str[0].unique())
    """ get address form title
    """
    df_['title_address'] = df_['title'].str.split('in ').str[-1]
    return df_


train_df_clean = extract_title_info(train_df_clean)
test_df = extract_title_info(test_df)

['sale']
['sale']


In [438]:
display(train_df_clean.loc[:, ['title_property_type','property_type']].head(3))
display(train_df_clean.loc[:, ['title_n_beds','num_beds']].head(3)) ## if hdb flat,can get from property_type
display(train_df_clean.loc[:, ['title_address','address']].head(3))

title_property_type property_type
0            hdb flat   hdb 4 rooms
1            hdb flat           hdb
2               condo         condo

title_n_beds  num_beds
0     hdb flat       3.0
1     hdb flat       4.0
2            4       4.0

title_address                             address
0           866 yishun street 81            sembawang / yishun (d27)
1  506b serangoon north avenue 4  hougang / punggol / sengkang (d19)
2                     meyerhouse                      128 meyer road

In [439]:
drop_attributes.add('title')

## 2. address
* no missing value
* not useful itself as one attribute for model
* maybe useful for impute subzone/ planning_area: 113 NaN

In [440]:
train_df_clean['address'].unique()

array(['sembawang / yishun (d27)', 'hougang / punggol / sengkang (d19)',
       '128 meyer road', ..., '52a toh tuck road', '22 west coast road',
       '10 sims drive'], dtype=object)

In [441]:
drop_attributes.add('address')

## 3. property_name
* no missing value
* not useful itself as one attribute for model

In [442]:
train_df['property_name'].unique()

array(['866 yishun street 81', 'hdb-serangoon estate', 'meyerhouse', ...,
       'signature park', 'raya garden', '241 yishun ring road'],
      dtype=object)

In [443]:
drop_attributes.add('property_name')

## 4. property_type
* useful as ordinal cat (possible ranking)

### dirty records
1. small letter
2. hdb vs hdb {n} rooms vs Hdb Executive
3. good class bungalow vs bungalow?
3. different type of house, condo
4. walk-up? land only?

In [444]:
fig = px.box(train_df_clean, x="property_type", y="price")
fig.show()

In [457]:
def preprocess_property_type(df) -> pd.DataFrame:
    df_ = df.copy()
    """ convert to small letters
    """
    df_['property_type'] = df_['property_type'].str.lower()

    """ drop hdb rooms: this feature will be reflected on num_beds	num_baths
    """
    df_.loc[df_['property_type'].str.contains('hdb'), 'property_type'] = 'hdb'
    
    cat_order = df_.groupby('property_type').mean().sort_values('price').index.to_list()
    enc = OrdinalEncoder(categories=[cat_order])
    df_['property_type_cat'] = enc.fit_transform(df_['property_type'].values.reshape(-1, 1))

    return df_

In [458]:
train_df_clean = preprocess_property_type(train_df_clean)#[['title_property_type','property_type','property_type_info']]

In [517]:
fig = px.box(train_df_clean.sort_values('price'), x="property_type", y="price")
fig.update_xaxes(categoryorder='array',categoryarray = train_df_clean.groupby('property_type').mean().sort_values('price').index.to_list())
fig.show()
fig = px.scatter(train_df_clean.groupby('property_type_cat').mean().sort_values('price').reset_index(), x="property_type_cat", y="price")
fig.show()

In [460]:
drop_attributes.add('property_type')

## tenure
* missing 1723

In [461]:
train_df_clean['tenure'].isnull().sum()

1723

In [462]:
fig = px.box(train_df_clean, x="tenure", y="price")
fig.show()

In [472]:
# train_df_clean.groupby('tenure').count()
fig = px.histogram(train_df_clean, x='tenure')
fig.show()

![alt text](../ref/lease.png "tenure type")

In [490]:
def pre_processing_tenure(df) -> pd.DataFrame:
    df_ = df.copy()
    """ ref https://www.theorigins.com.sg/post/freehold-vs-leasehold-condo-is-99-years-really-enough
    """
    df_.loc[train_df_clean['tenure'].isna(), 'tenure'] = ''
    df_.loc[df_['tenure'].str.contains(r'^1[0-9]{2}-year leasehold$'), 'tenure'] = '103/110-year leasehold'
    df_.loc[df_['tenure'].str.contains(r'^9[0-9]{2}-year leasehold$'), 'tenure'] = '999-year leasehold'
    df_.loc[df_['property_type']=='hdb', 'tenure'] = '99-year leasehold'
    return df_

In [491]:
# train_df_clean.groupby('tenure').count()
fig = px.histogram(pre_processing_tenure(train_df_clean), x='tenure')
fig.show()

In [494]:
temp_df = pre_processing_tenure(train_df_clean)
fig = px.histogram(temp_df[temp_df['tenure']==''], x='property_type')
fig.show()

In [501]:
print(temp_df.groupby('tenure').apply(lambda x: x['property_type'].unique())['103/110-year leasehold'])
print(temp_df.groupby('tenure').apply(lambda x: x['property_type'].unique())['99-year leasehold'])

print(temp_df.groupby('tenure').apply(lambda x: x['property_type'].unique())['999-year leasehold'])
print(temp_df.groupby('tenure').apply(lambda x: x['property_type'].unique())['freehold'])

['condo' 'bungalow' 'cluster house' 'terraced house' 'apartment'
 'semi-detached house']
['hdb' 'condo' 'terraced house' 'apartment' 'executive condo' 'bungalow'
 'landed' 'semi-detached house' 'cluster house' 'corner terrace'
 'townhouse' 'land only' 'walk-up' 'good class bungalow']
['bungalow' 'corner terrace' 'condo' 'semi-detached house' 'apartment'
 'terraced house' 'townhouse' 'walk-up' 'cluster house' 'landed']
['condo' 'semi-detached house' 'apartment' 'terraced house' 'bungalow'
 'corner terrace' 'land only' 'townhouse' 'cluster house'
 'conservation house' 'walk-up' 'landed' 'good class bungalow' 'shophouse']


In [519]:
temp2_df=temp_df[temp_df['property_type'].isin(temp_df[temp_df['tenure']=='']['property_type'].unique())].groupby('property_type').apply(lambda x: x['tenure'].unique()).reset_index().rename(columns={0: "possible_tenure"})
# temp2_df[temp2_df['property_type']=='apartment']['possible_tenure'].values
temp2_df

property_type                                    possible_tenure
0            apartment  [99-year leasehold, freehold, 999-year leaseho...
1             bungalow  [999-year leasehold, freehold, 99-year leaseho...
2        cluster house  [103/110-year leasehold, 99-year leasehold, fr...
3   conservation house                                       [freehold, ]
4       corner terrace  [999-year leasehold, , freehold, 99-year lease...
5               landed  [99-year leasehold, freehold, 999-year leaseho...
6  semi-detached house  [freehold, , 999-year leasehold, 99-year lease...
7       terraced house  [99-year leasehold, , freehold, 103/110-year l...

conservation house => freehold
